In [59]:
import numpy as np
import pandas as pd
import sys
import os
from codebase.file_utils import save_obj, load_obj
from codebase.post_process import samples_to_df, get_topn_eig
import altair as alt
alt.data_transformers.disable_max_rows()

%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [86]:
ppp = False
num_of_factors = 3
log_dir = "./log/FND/CV/20200423_030715_FND3fac_u_cv_s2m6/"
data = load_obj('data', log_dir)


if ppp: 
    ps = load_obj('ps', log_dir)
    ps.keys()
else: 
    print("\n\nChecking data integrity...\n\n")
    complete_data = load_obj("complete_data", log_dir)

    model_posterior_samples = dict()
    model_posterior_samples[0] = load_obj('ps_0', log_dir)
    model_posterior_samples[1] = load_obj('ps_1', log_dir)
    model_posterior_samples[2] = load_obj('ps_2', log_dir)





Checking data integrity...




In [87]:
data

{'D': array([[0, 0, 0, 0, 0, 1],
        [0, 0, 1, 0, 1, 0],
        [0, 0, 0, 0, 1, 1],
        ...,
        [0, 1, 1, 0, 0, 0],
        [0, 0, 0, 0, 0, 1],
        [0, 0, 1, 0, 0, 0]]), 'N': 565, 'J': 6, 'K': 3}

In [88]:
print(open(log_dir+'model.txt').read())

data {
  int<lower=1> N;
  int<lower=1> K;
  int<lower=1> J;
  int<lower=0, upper=1> DD[N, J];
}

transformed data{
  cov_matrix[J] I_J = diag_matrix(rep_vector(1, J));
}

parameters {
  vector[J] alpha;
  matrix[J,K] beta;
  matrix[N,J] yy;
  cov_matrix[J] Omega_cov;
}

transformed parameters{
  cov_matrix[J] Marg_cov;
  Marg_cov = beta * beta'+ Omega_cov;
}

model {
  to_vector(beta) ~ normal(0, 1);
  to_vector(alpha) ~ normal(0, 10);
  Omega_cov ~ inv_wishart(J+6, I_J);
  for (n in 1:N) yy[n,] ~ multi_normal(alpha, Marg_cov);
  for (j in 1:J) DD[, j] ~ bernoulli_logit(yy[, j]);
}

generated quantities{
  matrix[J,J] betabeta =  beta * beta';
}



In [98]:

if ppp:
    num_chains = ps['alpha'].shape[1]
    num_samples = ps['alpha'].shape[0]
    ps['beta_rot'] = np.empty_like(ps['beta'])

    for chain_number in range(ps['alpha'].shape[1]):
        if ps['beta'].ndim > 3:
            for i in range(num_samples):
                b = ps['beta'][i,chain_number]
                ps['beta_rot'][i,chain_number] = get_topn_eig(b@b.T, num_of_factors)['P']

else: 
    num_chains = model_posterior_samples[0]['alpha'].shape[1]
    num_samples = model_posterior_samples[0]['alpha'].shape[0]
    for j in range(3):
        beta_rot = np.empty_like(model_posterior_samples[j]['beta'])
        for chain_number in range(ps['alpha'].shape[1]):
            for i in range(num_samples):
                b = model_posterior_samples[j]['beta'][i,chain_number]
                beta_rot[i,chain_number] = get_topn_eig(b@b.T, num_of_factors)['P']
        model_posterior_samples[j]['beta_rot']= beta_rot

In [99]:
samples_to_df(model_posterior_samples[0], 'beta_rot').head()

index       val param_name  cn  row  col
0      0  0.644579   beta_rot   0    0    0
1      1  0.657846   beta_rot   0    0    0
2      2  0.577961   beta_rot   0    0    0
3      3  0.605529   beta_rot   0    0    0
4      4  0.587583   beta_rot   0    0    0

In [100]:
plotdata = samples_to_df(model_posterior_samples[0], 'beta')
c1 = alt.Chart(plotdata[plotdata.cn == 0]).mark_line(opacity=0.8).encode(
    alt.X('index:O'),
    alt.Y('val'),
    alt.Color('cn:N'),
    row = 'row:O',
    column= 'col:O'
).properties(width = 200, height=100, title='Beta') 

c1.interactive()

alt.Chart(...)

In [101]:
plotdata = samples_to_df(model_posterior_samples[0], 'beta_rot')
c1 = alt.Chart(plotdata[plotdata.cn == 0]).mark_line(opacity=0.8).encode(
    alt.X('index:O'),
    alt.Y('val'),
    alt.Color('cn:N'),
    row = 'row:O',
    column= 'col:O'
).properties(width = 200, height=100, title='Beta') 

c1.interactive()

alt.Chart(...)

In [71]:
np.round(np.mean(np.mean(ps['beta_rot'],0),0),2)

array([[ 0.45,  0.12],
       [ 0.31, -0.02],
       [ 0.5 , -0.08],
       [ 0.26,  0.08],
       [ 0.32,  0.07],
       [ 0.47,  0.11]])

In [46]:
np.round(np.mean(ps['beta_rot'],0),2)

array([[[0.44, 0.44],
        [0.33, 0.33],
        [0.52, 0.52],
        [0.24, 0.24],
        [0.31, 0.31],
        [0.47, 0.47]],

       [[0.45, 0.45],
        [0.29, 0.29],
        [0.51, 0.51],
        [0.25, 0.25],
        [0.32, 0.32],
        [0.47, 0.47]],

       [[0.46, 0.46],
        [0.3 , 0.3 ],
        [0.46, 0.46],
        [0.28, 0.28],
        [0.32, 0.32],
        [0.49, 0.49]],

       [[0.45, 0.45],
        [0.3 , 0.3 ],
        [0.49, 0.49],
        [0.27, 0.27],
        [0.33, 0.33],
        [0.47, 0.47]]])

In [16]:
c1 = alt.Chart(samples_to_df(ps, 'alpha')).mark_line(opacity=0.8).encode(
    alt.X('index:O'),
    alt.Y('val'),
    alt.Color('cn:N'),
    row = 'row:O',
    column= 'cn:N'
).properties(width = 200, height=100) 

c1.interactive()

alt.Chart(...)